In [2]:
import os
import sys
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path: # To be able to import files 
    sys.path.append(module_path) # without installing the project

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

from bayesrul.utils.plotting import (
    ResultSaver
)
from bayesrul.utils.post_process import (
    addFlightHours, addTestFlightInfo, post_process, smooth_some_columns
)

import altair as alt


In [7]:
path = '../results/ncmapss/bayesian/'
model_name = 'RADIAL'

saver = ResultSaver(path+model_name, filename = "results.parquet")
df = saver.load()
df = post_process(df, sigma=1.96)
df.head()

preds  labels       stds  unweighted_pred_loc    pred_var      ep_var  \
0  56.536930    66.0  15.223744            40.696735  644.541870  493.607147   
1  55.348103    66.0  15.724178            39.966625  646.703735  494.358826   
2  55.965202    66.0  14.919944            41.596283  622.204285  468.434448   
3  56.754673    66.0  13.987550            44.196781  538.606506  379.238159   
4  54.914726    66.0  13.875735            44.545273  488.086548  328.484436   

       al_var  preds_minus  preds_plus  ds_id  unit_id  win_id  engine_id  \
0  150.934753    26.698391   86.375473      4        7       0          0   
1  152.344940    24.528713   86.167496      4        7       1          0   
2  153.769821    26.722113   85.208290      4        7       2          0   
3  159.368347    29.339075   84.170273      4        7       3          0   
4  159.602127    27.718285   82.111168      4        7       4          0   

   flight_hours  
0      0.000000  
1      0.027879  
2      0.055759  
3      0.083638  
4      0.111517

In [8]:
engine = df[df.engine_id == 1]
engine = smooth_some_columns(
    engine, ['labels', 'preds', 'preds_plus', 'preds_minus'], bandwidth = [0.05, 0.01, 0.01, 0.01]
)

alt.data_transformers.disable_max_rows()

base = alt.Chart(engine).transform_calculate(
    true="'True RUL'",
    pred="'Predicted RUL'",
    interval="'95% CI'",
)

scale = alt.Scale(domain=["True RUL", "Predicted RUL", "95% CI"], range=['black', 'darkblue', 'lightblue'])

labels = base.mark_line(color='red').encode(
    x = alt.X("flight_hours", title="Flight hours"),
    y = alt.Y("labels_smooth", scale=alt.Scale(domain=(0, 100), clamp=True), 
                title="RUL (in number of cycles)"),
    color = alt.Color('true:N', scale=scale, title='')
    )

preds = base.mark_line(color='black').encode(
        x = alt.X("flight_hours", title="Flight hours"),
        y = alt.Y("preds_smooth"), 
        color = alt.Color('pred:N', scale=scale, title='')
    )

confidence = base.mark_area(opacity=0.9, color="#9ecae9").encode(
        x = alt.X("flight_hours", title="Flight hours"),
        y = alt.Y("preds_minus_smooth"), 
        y2 = alt.Y2("preds_plus_smooth"),
        color=alt.Color('interval:N', scale=scale, title='')
    )

chart = alt.layer(
    confidence + preds + labels
).configure_legend(
    strokeColor='gray',
    fillColor='#EEEEEE',
    padding=15,
    #offset=20,
    cornerRadius=10,
    orient='top-right',
    labelFont='sans-serif',
).properties(width=750)\
    .configure_axisY(titleAngle=0, titleY=-10, titleAnchor="start")\
    .configure_axisX(titleAngle=0, titleY=26)\
    .configure_axis(titleFontSize=16, labelFontSize=12)

# TO EXPORT AS PDF (Vectorized)
# inkscape -D -z --file=rul.svg --export-pdf=rul.pdf

chart

alt.LayerChart(...)

In [13]:
engine = df[df.engine_id == 0]
engine = smooth_some_columns(
    engine, ['labels', 'preds', 'preds_plus', 'preds_minus'], bandwidth = [0.05, 0.01, 0.01, 0.01]
)

alt.data_transformers.disable_max_rows()

base = alt.Chart(engine).transform_calculate(
    true="'True RUL'",
    pred="'Predicted RUL'",
    interval="'95% CI'",
)

scale = alt.Scale(domain=["True RUL", "Predicted RUL", "95% CI"], range=['black', 'darkblue', 'lightblue'])

labels = base.mark_line(color='red').encode(
    x = alt.X("flight_hours", title="Flight hours"),
    y = alt.Y("labels_smooth", scale=alt.Scale(domain=(0, 100), clamp=True), 
                title="RUL (in number of cycles)"),
    color = alt.Color('true:N', scale=scale, title='')
    )

preds = base.mark_line(color='black').encode(
        x = alt.X("flight_hours", title="Flight hours"),
        y = alt.Y("preds_smooth"), 
        color = alt.Color('pred:N', scale=scale, title='')
    )

confidence = base.mark_area(opacity=0.9, color="#9ecae9").encode(
        x = alt.X("flight_hours", title="Flight hours"),
        y = alt.Y("preds_minus_smooth"), 
        y2 = alt.Y2("preds_plus_smooth"),
        color=alt.Color('interval:N', scale=scale, title='')
    )

chart = alt.layer(
    confidence + preds + labels
).configure_legend(
    strokeColor='gray',
    fillColor='#EEEEEE',
    padding=15,
    #offset=20,
    cornerRadius=10,
    orient='top-right',
    labelFont='sans-serif',
).properties(width=750)\
    .configure_axisY(titleAngle=0, titleY=-10, titleAnchor="start")\
    .configure_axisX(titleAngle=0, titleY=26)\
    .configure_axis(titleFontSize=16, labelFontSize=12)

# TO EXPORT AS PDF (Vectorized)
# inkscape -D -z --file=rul.svg --export-pdf=rul.pdf

chart